In [3]:
from utils.BackTest import Engine, Strategy
import pandas as pd

In [4]:
df = pd.read_csv("../data/processed/btc_usdt_hourly_processed_with_sentiment.csv")

In [3]:
df = df.rename(columns={'OPEN':'Open','HIGH':'High','LOW':'Low','CLOSE':'Close','VOLUME':'Volume'})

In [4]:
df['Close']

0        51126.00
1        50911.11
2        51053.07
3        51139.14
4        51103.76
          ...    
8105    104998.35
8106    105030.40
8107    104630.03
8108    104715.29
8109    104818.69
Name: Close, Length: 8110, dtype: float64

In [ ]:
class SMACrossOver(Strategy):
    def on_bar(self):
        # Get current bar data
        current_bar = self.data.loc[self.current_idx]
        close = current_bar['Close']
        sma20 = current_bar['SMA20']
        sma50 = current_bar['SMA50']

        # For multiple positions, get all BTC positions
        btc_positions = [p for p in self.positions if p.ticker == 'BTC']

        # Buy signal: SMA20 > SMA50, and we allow up to 5 positions.
        if sma20 > sma50:
            if len(btc_positions) < 5:
                # Use 10% of available cash to determine the order size.
                order_size = 0.1 * self.cash / close
                self.buy('BTC', order_size)
                print(f"{self.current_idx} BUY signal: entering new position, order size {order_size:.4f}")
            else:
                print(f"{self.current_idx} BUY signal: maximum BTC positions reached.")


In [7]:
df['SMA50'] = df['Close'].rolling(window=50).mean()

In [8]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8110 entries, 0 to 8109
Data columns (total 32 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   datetime                    8110 non-null   object 
 1   Open                        8110 non-null   float64
 2   High                        8110 non-null   float64
 3   Low                         8110 non-null   float64
 4   Close                       8110 non-null   float64
 5   TOTAL_TRADES                8110 non-null   int64  
 6   TOTAL_TRADES_BUY            8110 non-null   int64  
 7   TOTAL_TRADES_SELL           8110 non-null   int64  
 8   Volume                      8110 non-null   float64
 9   VOLUME_BUY                  8110 non-null   float64
 10  VOLUME_SELL                 8110 non-null   float64
 11  return                      8110 non-null   float64
 12  log_return                  8110 non-null   float64
 13  hourly_volatility           8110 

In [9]:
df['datetime'] = pd.to_datetime(df['datetime'])
df = df.set_index('datetime')

In [10]:
df_filtered = df.dropna()
df_filtered

Open       High        Low      Close  \
datetime                                                                
2024-02-25 15:00:00+00:00   51741.22   51759.73   51436.67   51524.02   
2024-02-25 16:00:00+00:00   51524.02   51626.00   51279.80   51378.48   
2024-02-25 17:00:00+00:00   51378.48   51578.44   51355.51   51559.97   
2024-02-25 18:00:00+00:00   51559.97   51579.99   51498.83   51579.98   
2024-02-25 19:00:00+00:00   51579.98   51738.85   51510.79   51672.96   
...                              ...        ...        ...        ...   
2025-01-26 06:00:00+00:00  105094.12  105118.78  104959.20  104990.75   
2025-01-26 07:00:00+00:00  104990.75  105100.00  104950.00  104998.35   
2025-01-26 08:00:00+00:00  104998.35  105221.36  104863.31  105030.40   
2025-01-26 09:00:00+00:00  105030.40  105030.41  104444.01  104630.03   
2025-01-26 10:00:00+00:00  104630.03  104722.90  104500.00  104715.29   

                           TOTAL_TRADES  TOTAL_TRADES_BUY  TOTAL_TRADES_SELL  \
datetime                                                                       
2024-02-25 15:00:00+00:00         53527             23346              30181   
2024-02-25 16:00:00+00:00         67209             25481              41728   
2024-02-25 17:00:00+00:00         31868             16812              15056   
2024-02-25 18:00:00+00:00         25221             12205              13016   
2024-02-25 19:00:00+00:00         48954             18869              30085   
...                                 ...               ...                ...   
2025-01-26 06:00:00+00:00         38217             16739              21478   
2025-01-26 07:00:00+00:00         41775             22248              19527   
2025-01-26 08:00:00+00:00         63281             30294              32987   
2025-01-26 09:00:00+00:00         91103             41647              49456   
2025-01-26 10:00:00+00:00         50517             26960              23557   

                               Volume  VOLUME_BUY  VOLUME_SELL  ...  \
datetime                                                        ...   
2024-02-25 15:00:00+00:00  1040.13411   498.37362    541.76049  ...   
2024-02-25 16:00:00+00:00  1697.12356   796.34507    900.77849  ...   
2024-02-25 17:00:00+00:00   602.51743   302.10847    300.40896  ...   
2024-02-25 18:00:00+00:00   449.16565   233.62564    215.54001  ...   
2024-02-25 19:00:00+00:00  1106.98198   619.14466    487.83732  ...   
...                               ...         ...          ...  ...   
2025-01-26 06:00:00+00:00   243.85071    78.02352    165.82719  ...   
2025-01-26 07:00:00+00:00   208.35672   118.88131     89.47541  ...   
2025-01-26 08:00:00+00:00   283.50224   166.45833    117.04391  ...   
2025-01-26 09:00:00+00:00   621.23723   251.01916    370.21807  ...   
2025-01-26 10:00:00+00:00   252.60356   130.27092    122.33264  ...   

                           MACD_Hist        SMA20       STD20       Upper_BB  \
datetime                                                                       
2024-02-25 15:00:00+00:00 -23.898747   51618.0570   73.745272   51765.547544   
2024-02-25 16:00:00+00:00 -39.673459   51611.4040   88.405453   51788.214905   
2024-02-25 17:00:00+00:00 -36.846300   51611.2865   88.475658   51788.237815   
2024-02-25 18:00:00+00:00 -32.729348   51612.4550   87.867774   51788.190547   
2024-02-25 19:00:00+00:00 -23.288425   51617.6920   88.213188   51794.118376   
...                              ...          ...         ...            ...   
2025-01-26 06:00:00+00:00  25.310357  104868.2120  195.414461  105259.040923   
2025-01-26 07:00:00+00:00  21.256820  104884.5800  191.700229  105267.980457   
2025-01-26 08:00:00+00:00  19.272419  104898.4465  191.717112  105281.880725   
2025-01-26 09:00:00+00:00  -8.951024  104894.0960  196.965684  105288.027368   
2025-01-26 10:00:00+00:00 -21.128896  104899.8600  189.449989  105278.759979   

                                Lower_BB     RSI_14  smoothed_sentiment  \
d

In [11]:
e = Engine()
e.add_data(df_filtered)
e.add_strategy(SMACrossOver())
stats = e.run()     

  0%|          | 0/8060 [00:00<?, ?it/s]

2024-02-25 15:00:00+00:00 BUY signal: entering new position, order size 0.1941
Index: 2024-02-25 15:00:00+00:00 | Cash: 100000.00 | Total position value: 0.00 | Total value: 100000.00
2024-02-25 16:00:00+00:00 New position opened: <Position: BTC size: 0.19408423488695176 entry: 51524.02>
2024-02-25 16:00:00+00:00 BUY signal: entering new position, order size 0.1946
Index: 2024-02-25 16:00:00+00:00 | Cash: 90000.00 | Total position value: 9971.75 | Total value: 99971.75
2024-02-25 17:00:00+00:00 Take Profit Not Filled. Limit: 54100.221 / High: 51578.44
2024-02-25 17:00:00+00:00 Stop Loss Not Filled. Limit: 48947.818999999996 / Low: 51355.51
2024-02-25 17:00:00+00:00 New position opened: <Position: BTC size: 0.19463401797795496 entry: 51378.48>
2024-02-25 17:00:00+00:00 BUY signal: entering new position, order size 0.1939
Index: 2024-02-25 17:00:00+00:00 | Cash: 80000.00 | Total position value: 20042.30 | Total value: 100042.30
2024-02-25 18:00:00+00:00 Take Profit Not Filled. Limit: 541

  3%|▎         | 251/8060 [00:00<00:06, 1268.90it/s]

2024-03-01 10:00:00+00:00 Take Profit Not Filled. Limit: 64019.6655 / High: 62188.0
2024-03-01 10:00:00+00:00 Stop Loss Not Filled. Limit: 57922.5545 / Low: 61859.29
2024-03-01 10:00:00+00:00 Take Profit Not Filled. Limit: 64014.531 / High: 62188.0
2024-03-01 10:00:00+00:00 Stop Loss Not Filled. Limit: 57917.909 / Low: 61859.29
2024-03-01 10:00:00+00:00 Take Profit Not Filled. Limit: 64426.53 / High: 62188.0
2024-03-01 10:00:00+00:00 Stop Loss Not Filled. Limit: 58290.67 / Low: 61859.29
2024-03-01 10:00:00+00:00 Take Profit Not Filled. Limit: 64157.0895 / High: 62188.0
2024-03-01 10:00:00+00:00 Stop Loss Not Filled. Limit: 58046.890499999994 / Low: 61859.29
2024-03-01 10:00:00+00:00 Take Profit Not Filled. Limit: 63998.6655 / High: 62188.0
2024-03-01 10:00:00+00:00 Stop Loss Not Filled. Limit: 57903.5545 / Low: 61859.29
Index: 2024-03-01 10:00:00+00:00 | Cash: 57500.00 | Total position value: 50754.63 | Total value: 108254.63
2024-03-01 11:00:00+00:00 Take Profit Not Filled. Limit: 640

  5%|▍         | 378/8060 [00:00<00:06, 1230.18it/s]

...

2025-01-16 13:00:00+00:00 Stop Loss Not Filled. Limit: 92301.468 / Low: 98777.87
2025-01-16 13:00:00+00:00 Take Profit Not Filled. Limit: 101531.93400000001 / High: 99461.93
2025-01-16 13:00:00+00:00 Stop Loss Not Filled. Limit: 91862.226 / Low: 98777.87
2025-01-16 13:00:00+00:00 Take Profit Not Filled. Limit: 101375.442 / High: 99461.93
2025-01-16 13:00:00+00:00 Stop Loss Not Filled. Limit: 91720.63799999999 / Low: 98777.87
2025-01-16 13:00:00+00:00 Take Profit Not Filled. Limit: 101152.8 / High: 99461.93
2025-01-16 13:00:00+00:00 Stop Loss Not Filled. Limit: 91519.2 / Low: 98777.87
2025-01-16 13:00:00+00:00 Take Profit Not Filled. Limit: 104862.723 / High: 99461.93
2025-01-16 13:00:00+00:00 Stop Loss Not Filled. Limit: 94875.79699999999 / Low: 98777.87
2025-01-16 13:00:00+00:00 BUY signal: maximum BTC positions reached.
Index: 2025-01-16 13:00:00+00:00 | Cash: 75500.00 | Total position value: 50914.23 | Total value: 126414.23
2025-01-16 14:00:00+00:00 Take Profit Not Filled. Limit: 1

 99%|█████████▊| 7942/8060 [00:06<00:00, 926.65it/s]

2025-01-21 00:00:00+00:00 Stop Loss Not Filled. Limit: 98734.127 / Low: 101086.12
2025-01-21 00:00:00+00:00 Take Profit Not Filled. Limit: 108876.2115 / High: 102672.0
2025-01-21 00:00:00+00:00 Stop Loss Not Filled. Limit: 98507.0485 / Low: 101086.12
2025-01-21 00:00:00+00:00 Take Profit Not Filled. Limit: 108829.51800000001 / High: 102672.0
2025-01-21 00:00:00+00:00 Stop Loss Not Filled. Limit: 98464.802 / Low: 101086.12
2025-01-21 00:00:00+00:00 Take Profit Not Filled. Limit: 107725.8 / High: 102672.0
2025-01-21 00:00:00+00:00 Stop Loss Not Filled. Limit: 97466.2 / Low: 101086.12
2025-01-21 00:00:00+00:00 BUY signal: maximum BTC positions reached.
Index: 2025-01-21 00:00:00+00:00 | Cash: 77500.00 | Total position value: 48947.61 | Total value: 126447.61
2025-01-21 01:00:00+00:00 Take Profit Not Filled. Limit: 108111.48600000002 / High: 102233.26
2025-01-21 01:00:00+00:00 Stop Loss Not Filled. Limit: 97815.154 / Low: 100119.04
2025-01-21 01:00:00+00:00 Take Profit Not Filled. Limit: 1

100%|██████████| 8060/8060 [00:06<00:00, 1168.14it/s]

2025-01-24 01:00:00+00:00 Take Profit Not Filled. Limit: 108829.51800000001 / High: 103900.0
2025-01-24 01:00:00+00:00 Stop Loss Not Filled. Limit: 98464.802 / Low: 103039.87
2025-01-24 01:00:00+00:00 Take Profit Not Filled. Limit: 107725.8 / High: 103900.0
2025-01-24 01:00:00+00:00 Stop Loss Not Filled. Limit: 97466.2 / Low: 103039.87
Index: 2025-01-24 01:00:00+00:00 | Cash: 77500.00 | Total position value: 49937.59 | Total value: 127437.59
2025-01-24 02:00:00+00:00 Take Profit Not Filled. Limit: 108111.48600000002 / High: 103545.39
2025-01-24 02:00:00+00:00 Stop Loss Not Filled. Limit: 97815.154 / Low: 102956.72
2025-01-24 02:00:00+00:00 Take Profit Not Filled. Limit: 109127.19300000001 / High: 103545.39
2025-01-24 02:00:00+00:00 Stop Loss Not Filled. Limit: 98734.127 / Low: 102956.72
2025-01-24 02:00:00+00:00 Take Profit Not Filled. Limit: 108876.2115 / High: 103545.39
2025-01-24 02:00:00+00:00 Stop Loss Not Filled. Limit: 98507.0485 / Low: 102956.72
2025-01-24 02:00:00+00:00 Take P

In [12]:
e.plot()